# Scientific Collaboration Graph Analysis

In this jupyter notebook I will make the remaining needed analysis for my Graduation Final Project. 

## Environment setup

In [1]:
%pip install graphdatascience plotly pandas nbformat numpy


[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [2]:
from graphdatascience import GraphDataScience

host = "bolt://localhost:7687"
user = "neo4j"
password= "password"

gds = GraphDataScience(host, auth=(user, password))

/home/pedro.azevedo/Documents/repos/pfg/.venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Part 1: Attributing an Institution to Authors

Currently, there's no assignment of Institution to Authors. Instead, each author has one (or more) affiliations in each publication. This part of the analysis has the purpose of attributing a "home" Institution for each Author. For that, we will consider the institution the author has most the most affiliated publications.

We will create a new relationship `HOME_INSTITUTION`, like so:

```
(:Author)-[:HOME_INSTITUTION]->(:Intitution)
```

In [3]:
df_affcount = gds.run_cypher(
    """
    MATCH (a:Author)<-[:INVOLVES_AUTHOR]-(auth:Authorship)-[:INVOLVES_INSTITUTION]->(d:Institution)
    RETURN a.scopus_id AS author_id, a.name AS author_name,
       d.scopus_id AS institution_id, d.name AS institution_name,
       count(*) AS affiliation_count
    """
)

df_affcount

author_id            author_name institution_id  \
0       57217764581     Rodriguez, Juan C.       60032361   
1        7006818871    Wrobel, Luiz Carlos       60032361   
2        7005255555           Nunokawa, H.       60032361   
3        7006493149      Carvalho, I. C.S.       60032361   
4        6507364614     Ziolli, Roberta L.       60032361   
...             ...                    ...            ...   
248290  59695062000     Nogueira, André A.      130121784   
248291  57206291888    de Lima, Marcelo G.      105512226   
248292  59696345900      Kisil Marino, Ian      100998101   
248293   8856664000       Duque, Cristiane       60109712   
248294  57193992871  Theodoraki, Christina       60107071   

                                         institution_name  affiliation_count  
0       Pontifícia Universidade Católica do Rio de Jan...                  1  
1       Pontifícia Universidade Católica do Rio de Jan...                  9  
2       Pontifícia Universidade Católica do Rio de Jan...                  9  
3       Pontifícia Universidade Católica do Rio de Jan...                  4  
4       Pontifícia Universidade Católica do Rio de Jan...                  4  
...                                                   ...                ...  
248290                             Independent Researcher                  1  
248291            Center for Large Landscape Conservation                  1  
248292        Leibniz-Institut für Europäische Geschichte                  1  
248293                   Universidade Catolica Portuguesa                  1  
248294  Centre d'Etudes et de Recherche en Gestion d'A...                  1  

[248295 rows x 5 columns]

In [4]:
import pandas as pd
import plotly.express as px

# Filter for Unicamp affiliations
unicamp_affiliations = df_affcount[df_affcount["institution_id"] == "60029570"]

# Total affiliations per author
total_affiliations = df_affcount.groupby("author_id")["affiliation_count"].sum().rename("total_count")

# Merge and compute percentage
unicamp_affiliations = unicamp_affiliations.merge(total_affiliations, on="author_id", how="right").fillna({"affiliation_count": 0})
unicamp_affiliations["percentage"] = unicamp_affiliations["affiliation_count"] / unicamp_affiliations["total_count"]
unicamp_affiliations

author_id author_name institution_id institution_name  \
0       10038868400         NaN            NaN              NaN   
1       10039131200         NaN            NaN              NaN   
2       10039132600         NaN            NaN              NaN   
3       10039306300         NaN            NaN              NaN   
4       10039420200         NaN            NaN              NaN   
...             ...         ...            ...              ...   
181026   9943475600         NaN            NaN              NaN   
181027   9943485500         NaN            NaN              NaN   
181028   9943654300         NaN            NaN              NaN   
181029   9943745400         NaN            NaN              NaN   
181030   9943788900         NaN            NaN              NaN   

        affiliation_count  total_count  percentage  
0                     0.0            1         0.0  
1                     0.0           12         0.0  
2                     0.0            1         0.0  
3                     0.0            1         0.0  
4                     0.0            8         0.0  
...                   ...          ...         ...  
181026                0.0            1         0.0  
181027                0.0            1         0.0  
181028                0.0            1         0.0  
181029                0.0            9         0.0  
181030                0.0            2         0.0  

[181031 rows x 7 columns]

In [5]:
import numpy as np

# Define 20 bins between 0 and 1
bins = np.linspace(0, 1, 21)
unicamp_affiliations["binned"] = pd.cut(unicamp_affiliations["percentage"], bins=bins, include_lowest=True)
unicamp_affiliations["binned"] = unicamp_affiliations["binned"].astype(str)  # Convert to string for plotting


def bin_key(bin_str):
    # bin_str example: "[0.0, 0.05)"
    left = bin_str.split(",")[0].strip("[(")
    return float(left)

unique_bins = unicamp_affiliations["binned"].unique()
sorted_bins = sorted(unique_bins, key=bin_key)

fig = px.histogram(
    unicamp_affiliations,
    x="binned",
    category_orders={"binned": sorted_bins},
    title="Distribution of Author Affiliation % with Unicamp"
)
fig.update_layout(
    xaxis_title="Affiliation Percentage Bin",
    yaxis_title="Number of Authors"
)
fig.show()


A maioria dos autores tem todas as suas publicações associadas à Unicamp, ou nenhuma publicação associada à Unicamp.

In [8]:
unicamp_affiliations["unicamp"] = unicamp_affiliations["percentage"] > 0.5
unicamp_affiliations

author_id author_name institution_id institution_name  \
0       10038868400         NaN            NaN              NaN   
1       10039131200         NaN            NaN              NaN   
2       10039132600         NaN            NaN              NaN   
3       10039306300         NaN            NaN              NaN   
4       10039420200         NaN            NaN              NaN   
...             ...         ...            ...              ...   
181026   9943475600         NaN            NaN              NaN   
181027   9943485500         NaN            NaN              NaN   
181028   9943654300         NaN            NaN              NaN   
181029   9943745400         NaN            NaN              NaN   
181030   9943788900         NaN            NaN              NaN   

        affiliation_count  total_count  percentage          binned  unicamp  
0                     0.0            1         0.0  (-0.001, 0.05]    False  
1                     0.0           12         0.0  (-0.001, 0.05]    False  
2                     0.0            1         0.0  (-0.001, 0.05]    False  
3                     0.0            1         0.0  (-0.001, 0.05]    False  
4                     0.0            8         0.0  (-0.001, 0.05]    False  
...                   ...          ...         ...             ...      ...  
181026                0.0            1         0.0  (-0.001, 0.05]    False  
181027                0.0            1         0.0  (-0.001, 0.05]    False  
181028                0.0            1         0.0  (-0.001, 0.05]    False  
181029                0.0            9         0.0  (-0.001, 0.05]    False  
181030                0.0            2         0.0  (-0.001, 0.05]    False  

[181031 rows x 9 columns]

## Write back

Abaixo, vamos criar uma nova propriedade chamada `unicamp` para vértices do tipo `Author`. Essa propriedade é `true` se a porcentagem de afiliações do autor à Unicamp é estritamente superior a 0.5 (isto é, `percentage > 0.5`) e `false` caso contrário. Vamos usar essa porcentagem para classificar as comunidades entre comunidades "Unicamp" e "não-Unicamp".

In [7]:
batch_data = [
    {
        "author_id": row["author_id"],
        "unicamp": row["unicamp"]
    }
    for _, row in unicamp_affiliations.iterrows()
]

gds.run_cypher(
    """
    UNWIND $rows AS row
    MATCH (a:Author {scopus_id: row.author_id})
    SET a.unicamp = row.unicamp
    """,
    params={"rows": batch_data}
)

Empty DataFrame
Columns: []
Index: []